In [28]:
!pip install gql oauthlib requests_oauthlib > /dev/null

You should consider upgrading via the '/Users/triton/.pyenv/versions/3.9.2/bin/python3.9 -m pip install --upgrade pip' command.


In [6]:
import os
CLIENT_ID = os.getenv("CLIENT_ID")
CLIENT_SECRET = os.getenv("CLIENT_SECRET")
TENANT_ID = os.getenv("TENANT_ID")

In [10]:
import asyncio
import os

from oauthlib.oauth2 import BackendApplicationClient
from requests_oauthlib import OAuth2Session

from gql import Client, gql
from gql.transport.websockets import WebsocketsTransport

import pandas as pd

In [ ]:
# Taegis URLs
# Charlie/Production: "https://api.ctpx.secureworks.com"
# Delta: "https://api.delta.taegis.secureworks.com"
# Echo: "https://api.echo.taegis.secureworks.com"

# Taegis Events URLs
# Charlie/Production: "wss://api.ctpx.secureworks.com"
# Delta: "wss://api.delta.taegis.secureworks.com"
# Echo: "wss://api.echo.taegis.secureworks.com"

In [11]:
client = BackendApplicationClient(client_id=CLIENT_ID)
oauth_client = OAuth2Session(client=client)
token = oauth_client.fetch_token(
    token_url="https://api.ctpx.secureworks.com/auth/api/v2/auth/token",
    client_id=CLIENT_ID,
    client_secret=CLIENT_SECRET,
)

In [12]:
PAGE_SIZE = 10
MAX_ROWS = 50

QUERY_STR = "FROM process, persistence EARLIEST=-1d"

In [13]:
# https://gql.readthedocs.io/en/stable/transports/websockets.html
async def query(query_str: str, tenant_id: str, access_token: str):
    transport = WebsocketsTransport(
        url="wss://api.ctpx.secureworks.com/events/query",
        # not documented, reverse engineered from platform
        connect_args={
            "subprotocols": [
                "graphql-ws",
                f"x-tenant-context-{tenant_id}",
                f"access-token-{access_token}",
            ]
        },
    )

    async with Client(
        transport=transport,
        fetch_schema_from_transport=True,
    ) as session:

        # https://api-docs.taegis.secureworks.com/reference/#events-subscription-eventquery
        # https://api-docs.taegis.secureworks.com/reference/#events-eventquery
        # https://api-docs.taegis.secureworks.com/reference/#events-eventqueryresult
        subscription = gql(
            """subscription onEventQuery(
                            $query: String!,
                            $metadata: JSONObject,
                            $options: EventQueryOptions
                        ) {
                    eventQuery(query: $query, metadata: $metadata, options: $options) {
                        ...eventQueryResults
                        __typename
                    }
                }

                fragment eventQueryResults on EventQueryResults {
                    query {
                        id
                        query
                        status
                        reasons {
                            id
                            reason
                            __typename
                        }
                        submitted
                        completed
                        expires
                        types
                        metadata
                        __typename
                    }
                    result {
                        id
                        type
                        backend
                        status
                        reason
                        submitted
                        completed
                        expires
                        facets
                        rows
                        progress {
                            totalRows
                            totalRowsIsLowerBound
                            resultsTruncated
                            __typename
                        }
                        __typename
                    }
                    next
                    prev
                    __typename
                }"""
        )

        params = {
            "query": query_str,
            # https://api-docs.taegis.secureworks.com/reference/#events-eventqueryoptions
            "options": {
                "timestampAscending": True,
                "pageSize": PAGE_SIZE,
                "maxRows": MAX_ROWS,
                "skipCache": True,
            },
        }

        results = []
        async for result in session.subscribe(subscription, variable_values=params):
            results.append(result)

    # not documented
    # Taegis returns an empty result set to signify the
    # backend search page is finished
    # A single empty result set is sent for ALL pages
    # e.g., if 3 schemas a queried, expect up to 4 pages per page
    
    # We just remove the empty result set from our returned results
    return results[:-1]


async def query_paginate(next_page: str, tenant_id: str, access_token: str):
    transport = WebsocketsTransport(
        url="wss://api.ctpx.secureworks.com/events/query",
        # not documented, reverse engineered from platform
        connect_args={
            "subprotocols": [
                "graphql-ws",
                f"x-tenant-context-{tenant_id}",
                f"access-token-{access_token}",
            ]
        },
    )

    async with Client(
        transport=transport,
        fetch_schema_from_transport=True,
    ) as session:

        # https://api-docs.taegis.secureworks.com/reference/#events-subscription
        # https://api-docs.taegis.secureworks.com/reference/#events-eventquery
        # https://api-docs.taegis.secureworks.com/reference/#events-eventqueryresult
        subscription = gql(
            """subscription onEventPage($id: ID!) {
                eventPage(id: $id) {
                    ...eventQueryResults
                    __typename
                }
            }

            fragment eventQueryResults on EventQueryResults {
                query {
                    id
                    query
                    status
                    reasons {
                        id
                        reason
                        __typename
                    }
                    submitted
                    completed
                    expires
                    types
                    metadata
                    __typename
                }
                result {
                    id
                    type
                    backend
                    status
                    reason
                    submitted
                    completed
                    expires
                    facets
                    rows
                    progress {
                        totalRows
                        totalRowsIsLowerBound
                        resultsTruncated
                        __typename
                    }
                    __typename
                }
                next
                prev
                __typename
            }"""
        )

        params = {
            "id": next_page,
        }

        results = []
        async for result in session.subscribe(subscription, variable_values=params):
            results.append(result)

    # not documented
    # Taegis returns an empty result set to signify the
    # backend search page is finished
    # A single empty result set is sent for ALL pages
    # e.g., if 3 schemas a queried, expect up to 4 pages per page
    
    # We just remove the empty result set from our returned results
    return results[:-1]

In [14]:
def get_next_page(result_set, endpoint):
    # any or all the result sets can contain the the next reference
    # result schemas that max on results will not contain a next reference
    next_page = list(
        {
            result.get(endpoint, {}).get("next")
            for result in result_set
            if result.get(endpoint, {}).get("next")
        }
    )
    if next_page:
        return next_page[0]
    return None

async def run_query(query_str: str):
    results = await query(
        query_str=QUERY_STR,
        tenant_id=TENANT_ID,
        access_token=token.get("access_token"),
    )
    next_page = get_next_page(results, "eventQuery")
    
    while next_page:
        paginated_results = await query_paginate(
            next_page=next_page,
            tenant_id=TENANT_ID,
            access_token=token.get("access_token"),
        )

        next_page = get_next_page(paginated_results, "eventPage")
        results.extend(paginated_results)

    return results

In [15]:
results = await run_query(QUERY_STR)

In [16]:
len(results)

6

### Result Sets
- [eventQuery/eventPage](https://api-docs.taegis.secureworks.com/reference/#events-eventqueryresults)
    - [query](https://api-docs.taegis.secureworks.com/reference/#events-eventquery)
    - [result](https://api-docs.taegis.secureworks.com/reference/#events-eventqueryresult)

In [17]:
results[0]

{'eventQuery': {'query': {'id': '6ffba1b8605dea9a3b4a2e8f2db298bb091b2dd6',
   'query': 'FROM process, persistence EARLIEST=-1d',
   'status': 'RUNNING',
   'reasons': None,
   'submitted': '2022-02-04T20:01:48Z',
   'completed': None,
   'expires': '2022-03-05T20:01:48Z',
   'types': ['persistence', 'process'],
   'metadata': None,
   '__typename': 'EventQuery'},
  'result': {'id': '5ed31b7c4a2415d5aecfd60fccb1b063af4ace54',
   'type': 'persistence',
   'backend': 'Elasticsearch',
   'status': 'SUCCEEDED',
   'reason': '',
   'submitted': '2022-02-04T20:01:48Z',
   'completed': '2022-02-04T20:01:49Z',
   'expires': None,
   'facets': None,
   'rows': [],
   'progress': {'totalRows': 0,
    'totalRowsIsLowerBound': False,
    'resultsTruncated': False,
    '__typename': 'EventQueryProgress'},
   '__typename': 'EventQueryResult'},
  'next': None,
  'prev': None,
  '__typename': 'EventQueryResults'}}

In [18]:
# Make a data frame with full query
df = pd.json_normalize([
    row
    for result in results
    for row in result.get(list(result.keys())[0]).get("result",{}).get("rows", [])
])

In [19]:
df.shape

(50, 54)

In [20]:
df.head()

__store _file_schema_version _index_schema_version _kafka_offset  \
0        4             [0.83.3]              [0.83.3]  [6392549949]   
1        4             [0.83.3]              [0.83.3]  [6392549982]   
2        4             [0.83.3]              [0.83.3]  [6392549981]   
3        4             [0.83.3]              [0.83.3]  [6392549976]   
4        4             [0.83.3]              [0.83.3]  [6392549977]   

            _topic_partition allocations  \
0  [events.scwx.process-132]        None   
1  [events.scwx.process-132]        None   
2  [events.scwx.process-132]        None   
3  [events.scwx.process-132]        None   
4  [events.scwx.process-132]        None   

                                         commandline computer_name  \
0  /usr/sbin/logrotate /etc/logrotate.d/redcloakl...          None   
1                                                 sh          None   
2  /usr/sbin/logrotate /etc/logrotate.d/redcloakl...          None   
3                                 /usr/sbin/CRON -f           None   
4  /bin/sh -c /usr/sbin/logrotate /etc/logrotate....          None   

  event_time_fidelity   event_time_usec  ... visibility was_blocked  \
0               MICRO  1643918521000000  ...    PRIVATE        None   
1               MICRO  1643918581000000  ...    PRIVATE        None   
2               MICRO  1643918581000000  ...    PRIVATE        None   
3               MICRO  1643918582490000  ...    PRIVATE        None   
4               MICRO  1643918582500000  ...    PRIVATE        None   

  windows_sid os.arch     os.metaos     os.os  \
0        None    None  METAOS_POSIX  OS_LINUX   
1        None    None  METAOS_POSIX  OS_LINUX   
2        None    None  METAOS_POSIX  OS_LINUX   
3        None    None  METAOS_POSIX  OS_LINUX   
4        None    None  METAOS_POSIX  OS_LINUX   

                   program_hash.md5                         program_hash.sha1  \
0  ff9f6831debb63e53a31ff8057143af6  ab785ea7082e2c774adc71d36414fc7663533a7f   
1  1e6b1c887c59a315edb7eb9a315fc84c  803ffdb71aa236aa25009bef97db1b8ad0e3c62b   
2  ff9f6831debb63e53a31ff8057143af6  ab785ea7082e2c774adc71d36414fc7663533a7f   
3  2c82564ff5cc862c89392b061c7fbd59  1009594fbc8f9a95bd77af80b612171956c8853c   
4  1e6b1c887c59a315edb7eb9a315fc84c  803ffdb71aa236aa25009bef97db1b8ad0e3c62b   

  program_hash.sha256 program_hash.sha512  
0                None                None  
1                None                None  
2                None                None  
3                None                None  
4                None                None  

[5 rows x 54 columns]

In [22]:
# Filter rows to just process events
processes = pd.json_normalize([
    row
    for result in results
    for row in result.get(list(result.keys())[0]).get("result",{}).get("rows", [])
    if "process" in row.get("resource_id")
])

In [23]:
processes.shape

(50, 54)

In [24]:
processes.head()

__store _file_schema_version _index_schema_version _kafka_offset  \
0        4             [0.83.3]              [0.83.3]  [6392549949]   
1        4             [0.83.3]              [0.83.3]  [6392549982]   
2        4             [0.83.3]              [0.83.3]  [6392549981]   
3        4             [0.83.3]              [0.83.3]  [6392549976]   
4        4             [0.83.3]              [0.83.3]  [6392549977]   

            _topic_partition allocations  \
0  [events.scwx.process-132]        None   
1  [events.scwx.process-132]        None   
2  [events.scwx.process-132]        None   
3  [events.scwx.process-132]        None   
4  [events.scwx.process-132]        None   

                                         commandline computer_name  \
0  /usr/sbin/logrotate /etc/logrotate.d/redcloakl...          None   
1                                                 sh          None   
2  /usr/sbin/logrotate /etc/logrotate.d/redcloakl...          None   
3                                 /usr/sbin/CRON -f           None   
4  /bin/sh -c /usr/sbin/logrotate /etc/logrotate....          None   

  event_time_fidelity   event_time_usec  ... visibility was_blocked  \
0               MICRO  1643918521000000  ...    PRIVATE        None   
1               MICRO  1643918581000000  ...    PRIVATE        None   
2               MICRO  1643918581000000  ...    PRIVATE        None   
3               MICRO  1643918582490000  ...    PRIVATE        None   
4               MICRO  1643918582500000  ...    PRIVATE        None   

  windows_sid os.arch     os.metaos     os.os  \
0        None    None  METAOS_POSIX  OS_LINUX   
1        None    None  METAOS_POSIX  OS_LINUX   
2        None    None  METAOS_POSIX  OS_LINUX   
3        None    None  METAOS_POSIX  OS_LINUX   
4        None    None  METAOS_POSIX  OS_LINUX   

                   program_hash.md5                         program_hash.sha1  \
0  ff9f6831debb63e53a31ff8057143af6  ab785ea7082e2c774adc71d36414fc7663533a7f   
1  1e6b1c887c59a315edb7eb9a315fc84c  803ffdb71aa236aa25009bef97db1b8ad0e3c62b   
2  ff9f6831debb63e53a31ff8057143af6  ab785ea7082e2c774adc71d36414fc7663533a7f   
3  2c82564ff5cc862c89392b061c7fbd59  1009594fbc8f9a95bd77af80b612171956c8853c   
4  1e6b1c887c59a315edb7eb9a315fc84c  803ffdb71aa236aa25009bef97db1b8ad0e3c62b   

  program_hash.sha256 program_hash.sha512  
0                None                None  
1                None                None  
2                None                None  
3                None                None  
4                None                None  

[5 rows x 54 columns]

In [25]:
# Filter rows to just persistence events
persistence = pd.json_normalize([
    row
    for result in results
    for row in result.get(list(result.keys())[0]).get("result",{}).get("rows", [])
    if "persistence" in row.get("resource_id")
])

In [26]:
persistence.shape

(0, 0)

In [29]:
persistence.head()

Empty DataFrame
Columns: []
Index: []